![header](../figures/logos_partenaires._cmems_se.jpg)

# Western Mediterranean: Benchmark BFNQG plot maps
 

***
**Authors:**  CLS & Datlas <br>
**Copyright:** 2023 CLS & Datlas <br>
**License:** MIT

<div class="alert alert-block alert-success">
<h1><center>Western Mediterranean: Benchmark of BFNQG plot maps</center></h1>
<h5> The notebook aims to plot maps produced by the DUACS system. </h5>
    <h5> These maps are equivalent to the SEALEVEL_GLO_PHY_L4_MY_008_047 product distributed by the Copernicus Marine Service, except that a nadir altimeter (SARAL/Altika, SEALEVEL_GLO_PHY_L3_MY_008_062 product) has been excluded from the mapping. </h5>
        <h5> We provide below a demonstration of the validation of these maps against the independent SSH data from the Saral/AltiKa altimeter distributed by CMEMS </h5>
</div>

***
**General Note 1**: Execute each cell through the <button class="btn btn-default btn-xs"><i class="icon-play fa fa-play"></i></button> button from the top MENU (or keyboard shortcut `Shift` + `Enter`).<br>
<br>
**General Note 2**: If, for any reason, the kernel is not working anymore, in the top MENU, click on the <button class="btn btn-default btn-xs"><i class="fa fa-repeat icon-repeat"></i></button> button. Then, in the top MENU, click on "Cell" and select "Run All Above Selected Cell".<br>
***


<div class="alert alert-danger" role="alert">

<h3>Learning outcomes</h3>

At the end of this notebook you will know:
<ul>
  <li>How you can evaluated sea surface height maps with independent alongtrack data: statistical and spectral analysis</li>
</ul>
    
</div>

In [1]:
from glob import glob
import numpy as np
import os

In [2]:
import sys
sys.path.append('..')
from src.mod_plot import *
from src.mod_stat import *
from src.mod_spectral import *
from src.mod_interp import *
from src.mod_switchvar import *

In [3]:
import logging
logger = logging.getLogger()
logger.setLevel(logging.INFO)

<div class="alert alert-info" role="alert">

<h2>0. Parameters</h2>

</div>

In [4]:
time_min = '2019-01-15'                                        # time min for analysis
time_max = '2019-12-15'                                        # time max for analysis
output_dir = '../results'                                      # output directory path
os.system(f'mkdir -p {output_dir}')

# West Med region
region = 'WM'
lon_min = 1                                          # domain min longitude
lon_max = 20                                          # domain max longitude
lat_min = 30.                                          # domain min latitude
lat_max = 45.                                          # domain max latitude
box_lonlat = {'lon_min':lon_min,'lon_max':lon_max,'lat_min':lat_min,'lat_max':lat_max}

method_name = 'BFNQG'
 

<div class="alert alert-info" role="alert">

<h2>1. Input files</h2>

</div>

## Sea Surface Height maps to evaluate

In [5]:
%%time
list_of_maps = sorted(glob('../data/maps/DC_MapGlob_MedZoom_BFNQG/DC*.nc'))
ds_maps = xr.open_mfdataset(list_of_maps, combine='nested', concat_dim='time')
ds_maps = ds_maps.sel(time=slice(time_min, time_max))
ds_maps

CPU times: user 3.61 s, sys: 420 ms, total: 4.03 s
Wall time: 5.27 s


<xarray.Dataset>
Dimensions:  (time: 335, lat: 151, lon: 191)
Coordinates:
  * time     (time) datetime64[ns] 2019-01-15 2019-01-16 ... 2019-12-15
  * lon      (lon) float64 1.0 1.1 1.2 1.3 1.4 1.5 ... 19.6 19.7 19.8 19.9 20.0
  * lat      (lat) float64 30.0 30.1 30.2 30.3 30.4 ... 44.6 44.7 44.8 44.9 45.0
Data variables:
    sla      (time, lat, lon) float64 dask.array<chunksize=(1, 151, 191), meta=np.ndarray>
    pv       (time, lat, lon) float64 dask.array<chunksize=(1, 151, 191), meta=np.ndarray>

## Selecting only West Mediterranean

In [6]:

from src.mod_compare import regional_zoom
 
ds_maps = regional_zoom(ds_maps, [box_lonlat['lon_min'],box_lonlat['lon_max']], [box_lonlat['lat_min'],box_lonlat['lat_max']], namelon='lon', namelat='lat', change_lon=True)
ds_maps = ds_maps.rename({'lon':'longitude','lat':'latitude'})
ds_maps.sla.attrs = {'grid_mapping': 'crs',
                     'long_name': 'Sea level anomaly',
                     'standard_name': 'sea_surface_height_above_sea_level',
                     'units': 'm'}

## Plot BFNQG SLA movie

In [7]:
 
movie(ds_maps, 'sla', method=method_name, region=region, dir_output='../results/',dim_name=['time','latitude','longitude'],
          framerate=24,Display=True,clim=None,cmap='Spectral', newmovie=True)


## Compute and plot BFNQG geostrophic current movie

In [9]:
ds_maps = sla_to_ssh(ds_maps,'/Users/sammymetref/Documents/DATLAS/Data/cnes_obs-sl_glo_phy-mdt_my_0.125deg_P20Y_1695393893725_1mdt.nc')

u,v = ssh_to_currents(ds_maps.ssh, ds_maps.longitude, ds_maps.latitude)

ds_maps = ds_maps.assign(ugos=lambda ds_maps: ds_maps.sla*0  + u)
ds_maps.ugos.attrs = {'grid_mapping': 'crs',
                    'long_name': 'Absolute geostrophic velocity: zonal component',
                    'standard_name': 'surface_geostrophic_eastward_sea_water_velocity',
                    'units': 'm/s'}

ds_maps = ds_maps.assign(vgos=lambda ds_maps: ds_maps.sla*0  + v)
ds_maps.vgos.attrs = {'grid_mapping': 'crs',
                    'long_name': 'Absolute geostrophic velocity: meridian component',
                    'standard_name': 'surface_geostrophic_northward_sea_water_velocity',
                    'units': 'm/s'}

In [10]:
movie(ds_maps,name_var='uv', method=method_name, region=region, dir_output='../results/',dim_name=['time','latitude','longitude'],
          framerate=24,Display=True,clim=None,cmap='viridis', newmovie=True)


## Compute and plot BFNQG relative vorticity movie

In [10]:
rv = currents_to_relative_vorticity(np.array(ds_maps.ugos),np.array(ds_maps.vgos), ds_maps.longitude,ds_maps.latitude)

ds_maps = ds_maps.assign(rv=lambda ds_maps: ds_maps.sla * 0 + rv)

In [11]:
movie(ds_maps,name_var='rv', method=method_name, region=region, dir_output='../results/',dim_name=['time','latitude','longitude'],
          framerate=24,Display=True,clim=[-1,1],cmap='coolwarm', newmovie=True)
